In [1]:
# Preparation
import sys, os, time, csv
import glob
import datetime
from datetime import date
import random

import pymc as pm
import hddm
import kabuki

import arviz as az
import numpy as np
import pandas as pd
import feather
import xarray as xr
import matplotlib.pyplot as plt
import seaborn as sns
from patsy import dmatrix

from p_tqdm import p_map
from functools import partial

import argparse

# sys.path.append('../')
# sys.path.append('../model_code/')
# sys.path.append('../data_processing_code/')
sys.path.append('./')

from post_pred_gen_redifined import _parents_to_random_posterior_sample
from post_pred_gen_redifined import _post_pred_generate
from post_pred_gen_redifined import post_pred_gen

from pointwise_loglik_gen import _pointwise_like_generate
from pointwise_loglik_gen import pointwise_like_gen

# import self-defined functions
# from SimData import SimData
from hddm_to_InfData import hddm_to_InfData
from Def_Models import run_m0, run_m1, run_m2, run_m3,run_m4, run_m5, run_m6, run_m7

model_func = [run_m0, run_m1, run_m2, run_m3,run_m4, run_m5, run_m6, run_m7]

m_keys = ["ms0",
          "ms1",
          "ms2",
          "ms3",
          "ms4",
          "ms5",
          "ms6",
          "ms7"]

/opt/conda/lib/python3.7/site-packages/IPython/parallel.py:13: ShimWarning: The `IPython.parallel` package has been deprecated since IPython 4.0. You should import from ipyparallel instead.
  "You should import from ipyparallel instead.", ShimWarning)


In [2]:
os.getcwd()

'/home/jovyan/hddm/temp'

In [3]:
data = hddm.load_csv('/opt/conda/lib/python3.7/site-packages/hddm/examples/cavanagh_theta_nn.csv')

testMode = False

if testMode:
    runtime = '0'
    samples = 30
    burn = 10
    nppc = 8
    
    df_subj = data['subj_idx'].unique()
    # random select without repetition
    random.seed(10)
    indices = random.sample(range(len(df_subj)), 5)
    df_test_list = [df_subj[i] for i in sorted(indices)]    
    data = data[data['subj_idx'].isin(df_test_list)]
else:
    runtime = "1"
    samples = 5000
    burn = 2500
    nppc = 1000
    
chains = 4
savefile=True

In [4]:
%%time

# run all models
models, InfData = hddm_to_InfData(data=data,
                                  m_keys=m_keys, 
                                  model_func=model_func,
                                  runtime=runtime,
                                  samples = samples,
                                  burn=burn,
                                  nppc=nppc,
                                  chains=chains,
                                  savefile=True)

/opt/conda/lib/python3.7/site-packages/scipy/optimize/optimize.py:1985: RuntimeWarning: invalid value encountered in double_scalars
  tmp2 = (x - v) * (fx - fw)
/opt/conda/lib/python3.7/site-packages/scipy/optimize/optimize.py:1985: RuntimeWarning: invalid value encountered in double_scalars
  tmp2 = (x - v) * (fx - fw)
/opt/conda/lib/python3.7/site-packages/scipy/optimize/optimize.py:1985: RuntimeWarning: invalid value encountered in double_scalars
  tmp2 = (x - v) * (fx - fw)
/opt/conda/lib/python3.7/site-packages/scipy/optimize/optimize.py:1985: RuntimeWarning: invalid value encountered in double_scalars
  tmp2 = (x - v) * (fx - fw)


 -                 2%                  ] 143 of 5000 complete in 7.4 sec[                  0%                  ] 11 of 5000 complete in 0.5 sec[                  0%                  ] 12 of 5000 complete in 0.5 sec[                  0%                  ] 11 of 5000 complete in 0.5 sec[                  0%                  ] 22 of 5000 complete in 1.0 sec[                  0%                  ] 21 of 5000 complete in 1.0 sec[                  0%                  ] 21 of 5000 complete in 1.1 sec[                  0%                  ] 23 of 5000 complete in 1.1 sec[                  0%                  ] 32 of 5000 complete in 1.6 sec[                  0%                  ] 31 of 5000 complete in 1.5 sec[                  0%                  ] 33 of 5000 complete in 1.6 sec[                  0%                  ] 31 of 5000 complete in 1.6 sec[                  0%                  ] 42 of 5000 complete in 2.1 sec[                  0%                  ] 41 of 5000 complete in 2.1 sec[    

 [--                5%                  ] 292 of 5000 complete in 15.2 sec[--                6%                  ] 302 of 5000 complete in 15.5 sec[--                6%                  ] 305 of 5000 complete in 15.6 sec[--                6%                  ] 306 of 5000 complete in 15.7 sec[--                6%                  ] 302 of 5000 complete in 15.7 sec[--                6%                  ] 312 of 5000 complete in 16.0 sec[--                6%                  ] 315 of 5000 complete in 16.2 sec[--                6%                  ] 316 of 5000 complete in 16.2 sec[--                6%                  ] 312 of 5000 complete in 16.2 sec[--                6%                  ] 322 of 5000 complete in 16.6 sec[--                6%                  ] 325 of 5000 complete in 16.7 sec[--                6%                  ] 326 of 5000 complete in 16.7 sec[--                6%                  ] 322 of 5000 complete in 16.8 sec[--                6%                  ] 332 of 50

 [----             11%                  ] 585 of 5000 complete in 30.1 sec[----             11%                  ] 589 of 5000 complete in 30.2 sec[----             11%                  ] 585 of 5000 complete in 30.3 sec[----             11%                  ] 589 of 5000 complete in 30.3 sec[----             11%                  ] 595 of 5000 complete in 30.7 sec[----             12%                  ] 600 of 5000 complete in 30.8 sec[----             11%                  ] 595 of 5000 complete in 30.8 sec[----             11%                  ] 599 of 5000 complete in 30.8 sec[----             12%                  ] 605 of 5000 complete in 31.2 sec[----             12%                  ] 610 of 5000 complete in 31.3 sec[----             12%                  ] 605 of 5000 complete in 31.3 sec[----             12%                  ] 609 of 5000 complete in 31.3 sec[----             12%                  ] 615 of 5000 complete in 31.7 sec[----             12%                  ] 620 of 50

 [------           17%                  ] 870 of 5000 complete in 44.8 sec[------           17%                  ] 874 of 5000 complete in 44.8 sec[------           17%                  ] 863 of 5000 complete in 44.9 sec[------           17%                  ] 876 of 5000 complete in 45.2 sec[------           17%                  ] 880 of 5000 complete in 45.3 sec[------           17%                  ] 884 of 5000 complete in 45.3 sec[------           17%                  ] 873 of 5000 complete in 45.4 sec[------           17%                  ] 886 of 5000 complete in 45.7 sec[------           17%                  ] 894 of 5000 complete in 45.8 sec[------           17%                  ] 891 of 5000 complete in 45.8 sec[------           17%                  ] 883 of 5000 complete in 45.9 sec[------           17%                  ] 896 of 5000 complete in 46.2 sec[------           18%                  ] 904 of 5000 complete in 46.4 sec[------           18%                  ] 902 of 50

...

 [-----------------98%----------------- ] 4911 of 5000 complete in 5447.4 sec[-----------------97%----------------- ] 4890 of 5000 complete in 5447.7 sec[-----------------98%----------------- ] 4920 of 5000 complete in 5448.5 sec[-----------------99%----------------- ] 4979 of 5000 complete in 5448.7 sec[-----------------98%----------------- ] 4912 of 5000 complete in 5448.6 sec[-----------------97%----------------- ] 4891 of 5000 complete in 5448.8 sec[-----------------98%----------------- ] 4913 of 5000 complete in 5449.6 sec[-----------------99%----------------- ] 4980 of 5000 complete in 5449.8 sec[-----------------97%----------------- ] 4892 of 5000 complete in 5449.8 sec[-----------------98%----------------- ] 4921 of 5000 complete in 5450.1 sec[-----------------98%----------------- ] 4914 of 5000 complete in 5450.6 sec[-----------------99%----------------- ] 4981 of 5000 complete in 5450.8 sec[-----------------97%----------------- ] 4893 of 5000 complete in 5450.9 sec[----------

 [-----------------99%----------------- ] 4985 of 5000 complete in 5553.4 sec[-----------------99%----------------- ] 4986 of 5000 complete in 5554.6 sec[-----------------99%----------------- ] 4987 of 5000 complete in 5555.5 sec[-----------------99%----------------- ] 4988 of 5000 complete in 5556.5 sec[-----------------99%----------------- ] 4989 of 5000 complete in 5557.5 sec[-----------------99%----------------- ] 4990 of 5000 complete in 5558.5 sec[-----------------99%----------------- ] 4991 of 5000 complete in 5559.4 sec[-----------------99%----------------- ] 4992 of 5000 complete in 5560.5 sec[-----------------99%----------------- ] 4993 of 5000 complete in 5561.4 sec[-----------------99%----------------- ] 4994 of 5000 complete in 5562.4 sec[-----------------99%----------------- ] 4995 of 5000 complete in 5563.4 sec[-----------------99%----------------- ] 4996 of 5000 complete in 5564.4 sec[-----------------99%----------------- ] 4997 of 5000 complete in 5565.4 sec[----------

 [----------       28%                  ] 4 of 14 complete in 983.6 sec[----------       28%                  ] 4 of 14 complete in 984.2 sec[----------       28%                  ] 4 of 14 complete in 1001.1 sec[----------       28%                  ] 4 of 14 complete in 1004.5 sec[-------------    35%                  ] 5 of 14 complete in 1962.1 sec[-------------    35%                  ] 5 of 14 complete in 1968.1 sec[-------------    35%                  ] 5 of 14 complete in 1980.6 sec[-------------    35%                  ] 5 of 14 complete in 1981.9 sec[---------------- 42%                  ] 6 of 14 complete in 2883.9 sec[---------------- 42%                  ] 6 of 14 complete in 2891.8 sec[---------------- 42%                  ] 6 of 14 complete in 2905.2 sec[---------------- 42%                  ] 6 of 14 complete in 2922.8 sec[-----------------50%                  ] 7 of 14 complete in 3725.1 sec[-----------------50%                  ] 7 of 14 complete in 3735.4 sec[------

 [----------       28%                  ] 4 of 14 complete in 206.5 sec[----------       28%                  ] 4 of 14 complete in 206.7 sec[----------       28%                  ] 4 of 14 complete in 206.8 sec[----------       28%                  ] 4 of 14 complete in 213.7 sec[-------------    35%                  ] 5 of 14 complete in 413.2 sec[-------------    35%                  ] 5 of 14 complete in 414.6 sec[-------------    35%                  ] 5 of 14 complete in 416.5 sec[-------------    35%                  ] 5 of 14 complete in 426.0 sec[---------------- 42%                  ] 6 of 14 complete in 618.8 sec[---------------- 42%                  ] 6 of 14 complete in 621.0 sec[---------------- 42%                  ] 6 of 14 complete in 625.7 sec[---------------- 42%                  ] 6 of 14 complete in 640.1 sec[-----------------50%                  ] 7 of 14 complete in 799.0 sec[-----------------50%                  ] 7 of 14 complete in 799.6 sec[-----------------5

Adding these covariates:
['a_Intercept', "a_theta:C(conf, Treatment('LC'))[HC]", "a_theta:C(conf, Treatment('LC'))[LC]"]
Adding these covariates:
['a_Intercept', "a_theta:C(conf, Treatment('LC'))[HC]", "a_theta:C(conf, Treatment('LC'))[LC]"]
Adding these covariates:
['a_Intercept', "a_theta:C(conf, Treatment('LC'))[HC]", "a_theta:C(conf, Treatment('LC'))[LC]"]
Adding these covariates:
['a_Intercept', "a_theta:C(conf, Treatment('LC'))[HC]", "a_theta:C(conf, Treatment('LC'))[LC]"]


In [5]:
### compare models
tmp_loo_comp = az.compare(InfData, ic="loo")
tmp_loo_comp = tmp_loo_comp.reset_index()
tmp_waic_comp = az.compare(InfData, ic="waic")
tmp_waic_comp = tmp_waic_comp.reset_index()

tmp_dic = []
indx_name = []

for m_key, model in models.items():
    m_tmp = kabuki.utils.concat_models(model)
    tmp_dic.append(m_tmp.dic)
    indx_name.append(m_key)

tmp_dic_comp = pd.DataFrame(tmp_dic, index=indx_name, columns=['dic'])
tmp_dic_comp = tmp_dic_comp.sort_values(by=['dic'])
tmp_dic_comp = tmp_dic_comp.reset_index()
tmp_dic_comp.rename(columns={'index':'rank'}, inplace=True)


fname_dic = "Mod_Comp_dic_" + runtime + ".csv"
fname_loo = "Mod_Comp_loo_" + runtime + ".csv"
fname_waic = "Mod_Comp_waic_" + runtime + ".csv"
tmp_dic_comp.to_csv(fname_dic)
tmp_loo_comp.to_csv(fname_loo)
tmp_waic_comp.to_csv(fname_waic)

In [9]:
az.rhat(InfData['ms0'])

In [7]:
az.rhat(InfData['ms7'])

In [8]:
az.plot_ppc(InfData['ms7'])